In [29]:
import numpy as np
import numdifftools as nd
import matplotlib.pyplot as plt
import scipy.integrate as sp
import scipy.optimize

In [30]:
# parameter values
V1 = -1.2
V2 = 18.
V3 = 2.
V4 = 30.
phi = 0.04
VK = -84.
VL = -60.
VCa = 120.
gK = 8.
gL = 2.
gCa = 4.4
Cm = 20.
tend = 200
t = np.linspace(0,tend,10*tend)
initial = [-25., 0]
I0 = np.linspace(0,300,100)

In [3]:
# definition of the functions m_inf, w_inf and tau
def m_inf(V, V1, V2):
    return 0.5*(1+np.tanh((V-V1)/V2))
def w_inf(V, V3, V4):
    return 0.5*(1+np.tanh((V-V3)/V4))
def tau(V, V3, V4):
    return 1.0/np.cosh((V-V3)/(2*V4))

In [4]:
def MLmodel((V, w), t, V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0):
    dV = ((-gCa*m_inf(V, V1, V2)*(V-VCa)-gK*w*(V-VK)-gL*(V-VL))+I0)/Cm
    dw = phi *(w_inf(V, V3, V4)-w)/tau(V, V3, V4)
    return [dV, dw]

In [336]:
for i in range(len(I0)):
    s = sp.odeint(MLmodel, initial, t, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0[i]))
    plt.subplot(3,1,1)
    plt.title('V')
    plt.xlabel('time')
    plt.ylabel('V(t)')
    plt.axis([0,tend,-70,70])
    plt.plot(t,s[:,0], label=I0[i])
    plt.legend(loc='center right')
    plt.subplot(3,1,2)
    plt.title('w')
    plt.xlabel('time')
    plt.ylabel('w(t)')
    plt.axis([0,tend,0,0.8])
    plt.plot(t,s[:,1], label=I0[i])
    plt.subplot(3,1,3)
    plt.title('Phase plane')
    plt.xlabel('V')
    plt.ylabel('w')
    plt.axis([-70,70,0,1])
    plt.plot(s[:,0],s[:,1])
plt.tight_layout()
plt.show()

In [337]:
# nullclines
def null1(V, I0):
    return ((-gCa*m_inf(V, V1, V2)*(V-VCa)-gL*(V-VL))+I0)/(gK*(V-VK))
def null2(V):
    return w_inf(V, V3, V4)

In [347]:
# plotting nullcline n1 against different I0
listn1 = list()
listn2 = list()
vrange = np.linspace(-70,70,280)
for j in range(len(I0)):
    n1= list()
    n2 = list()
    for i in vrange:
        n1.append(null1(i, I0[j]))
        n2.append(null2(i))    
    listn1.append(n1)
    listn2.append(n2)
    plt.plot(vrange, n1, label='n1')
    plt.plot(vrange, n2, label='n2', color='black')
    plt.axis([-70,20,-.5,3])
    plt.xlabel('I0')
    plt.ylabel('n1')
plt.show()

In [45]:
stat=scipy.optimize.root(MLmodel,[-60,0],args=(t, V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0[1])).x
stat


array([ -5.94786440e+01,   1.63253471e-02])

In [52]:
# plotting the equilibrium agaist I0
stat = list()
for i in range(len(I0)):
    stat.append(scipy.optimize.root(MLmodel,[-60,0],args=(t, V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0[i])).x[0])
plt.plot(I0,stat)
plt.show()

In [5]:
# function to find the frequency
tend= 400
tsteps = 10*tend
trange=np.linspace(0,tend, tsteps)
def findFreq(s, start):
    start = start*10 # this is to calculated out the distortion because of the smaller than one stepsize in trange
    maxV_index = np.argmax(s[start:,0])
    maxV_next_index = np.argmax(s[start+maxV_index+1:,0])
    fV = (maxV_next_index+1)/10.0
    return fV

In [6]:
# list of frequencies for different I0
m = list()
I0 = np.linspace(50,250,400)
for i in range(len(I0)):
    s = sp.odeint(MLmodel, initial, trange, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0[i]))
    m.append(findFreq(s, 100))

In [7]:
plt.plot(I0,m)
plt.title('frequency over I0')
plt.show()

In [24]:
# function to find the amplitudes
def findAmp(s, start):
    max_index = np.argmax(s[start:,0])
    return s[start+max_index][0]
    

In [27]:
a = list()
I0 = np.linspace(0,300,100)
for i in range(len(I0)):
    s = sp.odeint(MLmodel, initial, trange, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0[i]))
    a.append(findAmp(s, 100))

In [28]:
plt.plot(I0,a)
plt.title('amplitude over I0')
plt.show()

In [65]:
# limited current impuls with the result, 
# that the system is beeing drawn from oszillation in the vicinity of the stationary point
def Istim(t):
    if 270 < t < 280:
        return 10.
    else:
        return 0

In [66]:
def model_stim((V, w), t,V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, I0):
    dV = ((-gCa*m_inf(V, V1, V2)*(V-VCa)-gK*w*(V-VK)-gL*(V-VL))+I0+Istim(t))/Cm
    dW = phi *(w_inf(V, V3, V4)-w)/tau(V, V3, V4)
    return [dV, dW]

In [70]:
tend= 1000
tsteps = 10*tend
trange=np.linspace(0,tend, tsteps)
solstim = sp.odeint(model_stim, initial, trange, args=(V1, V2, V3, V4, phi, VK, VL, VCa, gK, gL, gCa, Cm, 89))

In [72]:
plt.plot(trange,solstim[:,0])
plt.plot(range(len(t)),[0]*len(t), color = 'black')
plt.xlabel('time')
plt.ylabel('V')
plt.axis([0, tend, -60, 50])
plt.show()